# NBA Shot Selection Evolution (2000–2025)
This notebook uses `nba_api`, `pandas`, and `altair` to build interactive visualizations for an article-style narrative about how NBA shot selection and scoring geometry have changed from ~2000 to the present.

**Visualizations in this notebook:**

1. League-wide shot distribution timeline (stacked area, 2000–2025)
2. Event-driven turning points (annotated timeline)
3. Player-level shot selection evolution (interactive player dropdown)
4. Interactive / time-animated shot-chart heatmaps for selected players

> ⚠️ **Note:** This notebook is a template. You must run it in an environment with internet access and valid `nba_api` configuration. Some API calls may take time or require rate limiting.


In [262]:
# If needed, install dependencies (uncomment as appropriate)
# !pip install nba_api altair pandas

import time
import pandas as pd
import altair as alt

# Altair settings
alt.data_transformers.disable_max_rows()
alt.renderers.enable('default')

# nba_api imports
from nba_api.stats.endpoints import LeagueDashTeamShotLocations, PlayerDashboardByShootingSplits, ShotChartDetail, PlayerCareerStats
from nba_api.stats.static import players as static_players


In [263]:
### Helper functions

def season_str(start_year: int) -> str:
    # Return NBA season string like '2000-01' from starting year int.
    return f"{start_year}-{str(start_year + 1)[-2:]}"

def get_season_list(start=2000, end=2024):
    # Return list of season strings from start to end inclusive (e.g., 2000–2024 -> 2000-01..2024-25).
    return [season_str(y) for y in range(start, end + 1)]

def find_player_by_name(name: str):
    # Use nba_api static players to resolve a player's ID by full or partial name.
    all_players = static_players.get_players()
    matches = [p for p in all_players if name.lower() in p['full_name'].lower()]
    return matches  # list of dicts with 'id', 'full_name', etc.

SEASONS = get_season_list(2000, 2024)  # adjust end year as needed
SEASONS[:5], SEASONS[-5:]


(['2000-01', '2001-02', '2002-03', '2003-04', '2004-05'],
 ['2020-21', '2021-22', '2022-23', '2023-24', '2024-25'])

## 1. League-wide shot distribution timeline

We aggregate `LeagueDashTeamShotLocations` over all teams for each season, and compute the share of field-goal attempts by shot zone. We'll use the `By Zone` distance range, which returns standard NBA shot zones (e.g., Restricted Area, Mid-Range, Corner 3).


In [264]:
# Fetch league-wide shot distribution by season
# Results are cached to CSV to avoid repeated API calls

import os

CACHE_FILE = 'league_shot_zones_cache.csv'

# Try to load from cache first
if os.path.exists(CACHE_FILE):
    print(f'Loading cached data from {CACHE_FILE}...')
    df_league_raw = pd.read_csv(CACHE_FILE)
    print(f'Loaded {len(df_league_raw)} rows from cache.')
else:
    print('Cache not found. Fetching from NBA API...')
    zone_frames = []
    
    for season in SEASONS:
        print(f'Fetching LeagueDashTeamShotLocations for {season}...')
        try:
            resp = LeagueDashTeamShotLocations(
                season=season,
                season_type_all_star='Regular Season',
                distance_range='By Zone'
            )
            df = resp.get_data_frames()[0]
            df['SEASON'] = season
            zone_frames.append(df)
            time.sleep(1.0)  # basic rate limiting
        except Exception as e:
            print(f'Failed for {season}: {e}')
    
    df_league_raw = pd.concat(zone_frames, ignore_index=True)
    
    # Save to cache
    df_league_raw.to_csv(CACHE_FILE, index=False)
    print(f'Saved {len(df_league_raw)} rows to {CACHE_FILE}')

print("\nColumns in df_league_raw:", df_league_raw.columns.tolist())
df_league_raw.head()


Loading cached data from league_shot_zones_cache.csv...
Loaded 747 rows from cache.

Columns in df_league_raw: ['Unnamed: 0', 'Unnamed: 1', 'Restricted Area', 'Restricted Area.1', 'Restricted Area.2', 'In The Paint (Non-RA)', 'In The Paint (Non-RA).1', 'In The Paint (Non-RA).2', 'Mid-Range', 'Mid-Range.1', 'Mid-Range.2', 'Left Corner 3', 'Left Corner 3.1', 'Left Corner 3.2', 'Right Corner 3', 'Right Corner 3.1', 'Right Corner 3.2', 'Above the Break 3', 'Above the Break 3.1', 'Above the Break 3.2', 'Backcourt', 'Backcourt.1', 'Backcourt.2', 'Corner 3', 'Corner 3.1', 'Corner 3.2', 'SEASON']


Unnamed: 0         Unnamed: 1 Restricted Area Restricted Area.1  \
0     TEAM_ID          TEAM_NAME             FGM               FGA   
1  1610612737      Atlanta Hawks            1078              1819   
2  1610612738     Boston Celtics            1163              2158   
3  1610612766  Charlotte Hornets            1070              1824   
4  1610612741      Chicago Bulls            1024              1825   

  Restricted Area.2 In The Paint (Non-RA) In The Paint (Non-RA).1  \
0            FG_PCT                   FGM                     FGA   
1             0.593                   408                    1238   
2             0.539                   298                     829   
3             0.587                   325                     852   
4             0.561                   381                    1015   

  In The Paint (Non-RA).2 Mid-Range Mid-Range.1  ... Above the Break 3  \
0                  FG_PCT       FGM         FGA  ...               FGM   
1                    0.33      1057        2675  ...               249   
2                   0.359       721        1865  ...               419   
3                   0.381      1065        2842  ...               265   
4                   0.375       988        2623  ...               280   

  Above the Break 3.1 Above the Break 3.2 Backcourt Backcourt.1 Backcourt.2  \
0                 FGA              FG_PCT       FGM         FGA      FG_PCT   
1                 701               0.355         1          10         0.1   
2                1183               0.354         0          12         0.0   
3                 790               0.335         1           9       0.111   
4                 812               0.345         0           5         0.0   

  Corner 3 Corner 3.1 Corner 3.2   SEASON  
0      FGM        FGA     FG_PCT      NaN  
1       83        225      0.369  2000-01  
2      172        438      0.393  2000-01  
3       74        184      0.402  2000-01  
4       48        131      0.366  2000-01  

[5 rows x 27 columns]

In [265]:
# Transform league shot-location data into long format for Altair

# The CSV has a structure where columns are: TEAM_ID, TEAM_NAME, then zone data (FGM, FGA, FG_PCT per zone)
# Skip first row if it contains the header with zone names
print("Sample of raw data:")
print(df_league_raw.head())

# Define the zones we expect
zone_names = [
    'Restricted Area',
    'In The Paint (Non-RA)',
    'Mid-Range',
    'Left Corner 3',
    'Right Corner 3',
    'Above the Break 3',
    'Backcourt'
]

# Extract long format: for each team-season, get FGA for each zone
records = []
for idx, row in df_league_raw.iterrows():
    # Skip header row if it exists
    if row.get('Unnamed: 0') == 'TEAM_ID' or row.get('Unnamed: 1') == 'TEAM_NAME':
        continue
    
    season = row['SEASON']
    team_name = row.get('Unnamed: 1', 'Unknown')
    
    # For each zone, extract FGA (column pattern: zone, zone.1 (FGA), zone.2)
    for zone in zone_names:
        fga_col = f'{zone}.1'  # .1 suffix is FGA
        if fga_col in df_league_raw.columns:
            fga_value = row[fga_col]
            # Convert to float and check validity
            try:
                fga = float(fga_value)
                if pd.notna(fga) and fga >= 0:
                    records.append({
                        'SEASON': season,
                        'TEAM_NAME': team_name,
                        'SHOT_ZONE_BASIC': zone,
                        'FGA': fga
                    })
            except (ValueError, TypeError):
                continue

df_league_long = pd.DataFrame(records)

# Aggregate by season and zone (sum across all teams)
df_league = (
    df_league_long
    .groupby(['SEASON', 'SHOT_ZONE_BASIC'], as_index=False)['FGA']
    .sum()
)

# Compute share of FGA per season
df_league['TOTAL_FGA_SEASON'] = df_league.groupby('SEASON')['FGA'].transform('sum')
df_league['FGA_SHARE'] = df_league['FGA'] / df_league['TOTAL_FGA_SEASON']

print(f"\nTransformed {len(records)} records into {len(df_league)} aggregated zone-season combinations")
print("\nFinal league data:")
df_league.head(10)


Sample of raw data:
   Unnamed: 0         Unnamed: 1 Restricted Area Restricted Area.1  \
0     TEAM_ID          TEAM_NAME             FGM               FGA   
1  1610612737      Atlanta Hawks            1078              1819   
2  1610612738     Boston Celtics            1163              2158   
3  1610612766  Charlotte Hornets            1070              1824   
4  1610612741      Chicago Bulls            1024              1825   

  Restricted Area.2 In The Paint (Non-RA) In The Paint (Non-RA).1  \
0            FG_PCT                   FGM                     FGA   
1             0.593                   408                    1238   
2             0.539                   298                     829   
3             0.587                   325                     852   
4             0.561                   381                    1015   

  In The Paint (Non-RA).2 Mid-Range Mid-Range.1  ... Above the Break 3  \
0                  FG_PCT       FGM         FGA  ...               FGM

SEASON        SHOT_ZONE_BASIC      FGA  TOTAL_FGA_SEASON  FGA_SHARE
0  2000-01      Above the Break 3  24182.0          191662.0   0.126170
1  2000-01              Backcourt    298.0          191662.0   0.001555
2  2000-01  In The Paint (Non-RA)  30063.0          191662.0   0.156854
3  2000-01          Left Corner 3   3993.0          191662.0   0.020834
4  2000-01              Mid-Range  72687.0          191662.0   0.379246
5  2000-01        Restricted Area  56347.0          191662.0   0.293992
6  2000-01         Right Corner 3   4092.0          191662.0   0.021350
7  2001-02      Above the Break 3  26136.0          193251.0   0.135244
8  2001-02              Backcourt    311.0          193251.0   0.001609
9  2001-02  In The Paint (Non-RA)  28142.0          193251.0   0.145624

In [266]:
# Stacked area chart: league-wide shot distribution over time

shot_zone_order = [
    'Restricted Area',
    'In The Paint (Non-RA)',
    'Mid-Range',
    'Left Corner 3',
    'Right Corner 3',
    'Above the Break 3',
    'Backcourt'
]

chart_league = (
    alt.Chart(df_league)
    .mark_area()
    .encode(
        x=alt.X(
            'SEASON:O', 
            title='Season', 
            sort=SEASONS,
            scale=alt.Scale(domain=SEASONS, paddingOuter=0, paddingInner=0),
            axis=alt.Axis(
                labelAngle=-45,
                labelFontSize=12,
                titleFontSize=14,
                titleFontWeight='bold',
                titlePadding=10
            )
        ),
        y=alt.Y(
            'FGA_SHARE:Q', 
            stack='normalize', 
            axis=alt.Axis(
                format='%',
                labelFontSize=12,
                titleFontSize=14,
                titleFontWeight='bold',
                titlePadding=10
            ),
            title='Share of FGA'
        ),
        color=alt.Color(
            'SHOT_ZONE_BASIC:N', 
            title='Shot Zone', 
            sort=shot_zone_order,
            legend=alt.Legend(
                titleFontSize=14,
                titleFontWeight='bold',
                labelFontSize=12,
                symbolSize=200,
                symbolStrokeWidth=0,
                padding=10,
                cornerRadius=5
            )
        ),
        tooltip=[
            alt.Tooltip('SEASON:O', title='Season'),
            alt.Tooltip('SHOT_ZONE_BASIC:N', title='Zone'),
            alt.Tooltip('FGA_SHARE:Q', title='Shot Share', format='.1%'),
            alt.Tooltip('FGA:Q', title='FGA (agg)')
        ]
    )
    .properties(
        title=alt.Title(
            'League-wide Shot Distribution by Zone (2000–2025)',
            fontSize=16,
            fontWeight='bold',
            anchor='start',
            offset=10
        ),
        width=800,
        height=400
    )
)

chart_league


alt.Chart(...)

## 2. Event-driven turning points

We define a small table of key rule or strategy changes and annotate them on a timeline that shares the same x-axis as the league-wide chart. You can expand or refine this list for your narrative.


In [267]:
# Define key events manually
events_data = [
    {'SEASON': '2004-05', 'event': 'Hand-checking rules enforced on perimeter'},
    {'SEASON': '2012-13', 'event': 'Peak "Moreyball" era in Houston (3PT emphasis)'},
    {'SEASON': '2015-16', 'event': 'Stephen Curry unanimous MVP, pull-up 3 revolution'},
    {'SEASON': '2018-19', 'event': 'Freedom of movement rules emphasize spacing'},
]

df_events = pd.DataFrame(events_data)

# Create vertical rule marks for events (overlay on the league chart)
events_marks = (
    alt.Chart(df_events)
    .mark_rule(color='black', strokeWidth=2.5, opacity=0.8, strokeDash=[5,3])
    .encode(
        x=alt.X('SEASON:O', sort=SEASONS),
        tooltip=[
            alt.Tooltip('SEASON:O', title='Season'), 
            alt.Tooltip('event:N', title='Event')
        ]
    )
)

# Create text labels for events - positioned inside the plot near the lines
events_labels = (
    alt.Chart(df_events)
    .mark_text(
        align='center',
        baseline='bottom',
        dx=15,
        fontSize=12,
        angle=270,
        color='black',
        fontWeight='bold'
    )
    .encode(
        x=alt.X('SEASON:O', sort=SEASONS),
        y=alt.value(200),  # Position inside the plot area (middle-ish)
        text='event:N'
    )
)

# Layer events on top of the league-wide chart
chart_with_events = (chart_league + events_marks + events_labels).properties(
    title=alt.Title(
        'League-wide Shot Distribution by Zone with Key Events (2000–2025)',
        fontSize=16,
        fontWeight='bold',
        anchor='start',
        offset=10
    ),
    width=800,
    height=450
).configure_view(
    strokeWidth=0
)

chart_with_events


alt.LayerChart(...)

## 3. Player-level shot selection evolution

We now fetch shot-zone splits for selected star players (e.g., Stephen Curry, James Harden, LeBron James, Kevin Durant, DeMar DeRozan) and visualize how their shot mixes evolve over time.

> 💡 Tip: To avoid repetitive calls and rate limits, consider caching the `PlayerDashboardByShootingSplits` results per player to CSV/Parquet, then reloading for visualization.


In [268]:
# Define players of interest by name (we will look up their IDs)
player_names = [
    'Stephen Curry',
    'James Harden',
    'LeBron James',
    'Kevin Durant',
    'DeMar DeRozan'
]

# Resolve players and pick the first match for each name
player_map = {}
for name in player_names:
    matches = find_player_by_name(name)
    if not matches:
        print(f'No NBA API match found for {name}')
        continue
    player_map[name] = matches[0]['id']
    print(f"{name}: {matches[0]['id']}")

player_map


Stephen Curry: 201939
James Harden: 201935
LeBron James: 2544
Kevin Durant: 201142
DeMar DeRozan: 201942


{'Stephen Curry': 201939,
 'James Harden': 201935,
 'LeBron James': 2544,
 'Kevin Durant': 201142,
 'DeMar DeRozan': 201942}

In [269]:
# Fetch shooting splits for each player across all seasons
# Results are cached to CSV to avoid repeated API calls

PLAYER_CACHE_FILE = 'player_shot_zones_cache.csv'

# Try to load from cache first
if os.path.exists(PLAYER_CACHE_FILE):
    print(f'Loading cached player data from {PLAYER_CACHE_FILE}...')
    df_players_raw = pd.read_csv(PLAYER_CACHE_FILE)
    print(f'Loaded {len(df_players_raw)} rows from cache.')
else:
    print('Cache not found. Fetching from NBA API...')
    player_frames = []
    
    # Use ShotChartDetail to get shot zone data for each player across multiple seasons
    # We'll fetch a subset of seasons to show evolution (e.g., every 3 years from 2012-2024)
    seasons_to_fetch = ['2012-13', '2015-16', '2018-19', '2021-22', '2024-25']
    
    for name, pid in player_map.items():
        print(f'Fetching shot data for {name} (ID {pid}) across multiple seasons...')
        player_season_frames = []
        
        for season in seasons_to_fetch:
            try:
                # Fetch shot chart data for the player for this season
                resp = ShotChartDetail(
                    team_id=0,
                    player_id=pid,
                    season_type_all_star='Regular Season',
                    season_nullable=season,
                    context_measure_simple='FGA'
                )
                df_shots = resp.get_data_frames()[0]
                
                if not df_shots.empty and 'SHOT_ZONE_BASIC' in df_shots.columns:
                    # Aggregate by zone for this season
                    df_agg = (
                        df_shots.groupby('SHOT_ZONE_BASIC')
                        .agg(
                            FGA=('SHOT_MADE_FLAG', 'count'),
                            FGM=('SHOT_MADE_FLAG', 'sum')
                        )
                        .reset_index()
                    )
                    df_agg['SEASON_ID'] = season
                    df_agg['PLAYER_NAME'] = name
                    player_season_frames.append(df_agg)
                    print(f'  ✓ {season}: {len(df_shots)} shots')
                
                time.sleep(0.6)  # Rate limiting between seasons
                
            except Exception as e:
                print(f'  ✗ {season}: {e}')
        
        if player_season_frames:
            player_frames.extend(player_season_frames)
            print(f'  Total: {len(player_season_frames)} seasons fetched for {name}')
        else:
            print(f'  No data fetched for {name}')
    
    if player_frames:
        df_players_raw = pd.concat(player_frames, ignore_index=True)
        
        # Save to cache
        df_players_raw.to_csv(PLAYER_CACHE_FILE, index=False)
        print(f'Saved {len(df_players_raw)} rows to {PLAYER_CACHE_FILE}')
    else:
        print('No player data was fetched. Please check the API or player IDs.')
        df_players_raw = pd.DataFrame()

df_players_raw.head()


Loading cached player data from player_shot_zones_cache.csv...
Loaded 162 rows from cache.


SHOT_ZONE_BASIC  FGA  FGM SEASON_ID    PLAYER_NAME
0      Above the Break 3  505  225   2012-13  Stephen Curry
1              Backcourt    6    0   2012-13  Stephen Curry
2  In The Paint (Non-RA)  159   63   2012-13  Stephen Curry
3          Left Corner 3   54   26   2012-13  Stephen Curry
4              Mid-Range  467  203   2012-13  Stephen Curry

In [270]:
# Transform player shooting splits for visualization

# Typical columns: 'SEASON_ID', 'SHOT_ZONE_BASIC', 'FGA', 'FGM', etc.
df_players = df_players_raw.copy()
df_players.rename(columns={'SEASON_ID': 'SEASON'}, inplace=True)

# Compute per-season total FGA for each player
df_players['TOTAL_FGA_PLAYER_SEASON'] = df_players.groupby(['PLAYER_NAME', 'SEASON'])['FGA'].transform('sum')
df_players['FGA_SHARE'] = df_players['FGA'] / df_players['TOTAL_FGA_PLAYER_SEASON']

df_players.head()


SHOT_ZONE_BASIC  FGA  FGM   SEASON    PLAYER_NAME  \
0      Above the Break 3  505  225  2012-13  Stephen Curry   
1              Backcourt    6    0  2012-13  Stephen Curry   
2  In The Paint (Non-RA)  159   63  2012-13  Stephen Curry   
3          Left Corner 3   54   26  2012-13  Stephen Curry   
4              Mid-Range  467  203  2012-13  Stephen Curry   

   TOTAL_FGA_PLAYER_SEASON  FGA_SHARE  
0                     1388   0.363833  
1                     1388   0.004323  
2                     1388   0.114553  
3                     1388   0.038905  
4                     1388   0.336455

In [271]:
# Player-level shot selection evolution chart (interactive dropdown)

player_dropdown = alt.binding_select(options=sorted(df_players['PLAYER_NAME'].unique()), name='Player: ')
player_select = alt.selection_point(fields=['PLAYER_NAME'], bind=player_dropdown, value='Stephen Curry')

chart_player = (
    alt.Chart(df_players)
    .mark_area()
    .encode(
        x=alt.X(
            'SEASON:O', 
            title='Season',
            axis=alt.Axis(
                labelAngle=-45,
                labelFontSize=12,
                titleFontSize=14,
                titleFontWeight='bold',
                titlePadding=10
            )
        ),
        y=alt.Y(
            'FGA_SHARE:Q', 
            stack='normalize', 
            axis=alt.Axis(
                format='%',
                labelFontSize=12,
                titleFontSize=14,
                titleFontWeight='bold',
                titlePadding=10
            ),
            title='Share of FGA'
        ),
        color=alt.Color(
            'SHOT_ZONE_BASIC:N', 
            title='Shot Zone', 
            sort=shot_zone_order,
            legend=alt.Legend(
                titleFontSize=14,
                titleFontWeight='bold',
                labelFontSize=12,
                symbolSize=200,
                symbolStrokeWidth=0,
                padding=10,
                cornerRadius=5
            )
        ),
        tooltip=[
            alt.Tooltip('PLAYER_NAME:N', title='Player'),
            alt.Tooltip('SEASON:O', title='Season'),
            alt.Tooltip('SHOT_ZONE_BASIC:N', title='Zone'),
            alt.Tooltip('FGA_SHARE:Q', title='Shot Share', format='.1%'),
            alt.Tooltip('FGA:Q', title='FGA (zone)')
        ]
    )
    .add_params(player_select)
    .transform_filter(player_select)
    .properties(
        title=alt.Title(
            'Player Shot Selection Evolution by Zone',
            fontSize=16,
            fontWeight='bold',
            anchor='start',
            offset=10
        ),
        width=800,
        height=400
    )
).configure_view(
    strokeWidth=0
)

chart_player


alt.Chart(...)

## 4. Interactive shot-chart heatmaps over time

We use `ShotChartDetail` to obtain individual shot coordinates (`LOC_X`, `LOC_Y`) for each player and season. Then we create binned 2D heatmaps and add a season slider to show how shot locations migrate over time.

> ⚠️ These API calls can be heavy (one request per season per player). You may want to only pull a subset of seasons, or cache the results.


In [272]:
def fetch_shotchart_for_player_seasons(player_id: int, seasons: list, season_type='Regular Season'):
    frames = []
    for season in seasons:
        print(f'Fetching ShotChartDetail for player {player_id}, {season}...')
        try:
            resp = ShotChartDetail(
                team_id=0,
                player_id=player_id,
                season_type_all_star=season_type,
                season_nullable=season,
                context_measure_simple='FGA'
            )
            df = resp.get_data_frames()[0]
            df['SEASON'] = season
            frames.append(df)
            time.sleep(1.0)
        except Exception as e:
            print(f'Failed for {season}: {e}')
    if not frames:
        return pd.DataFrame()
    return pd.concat(frames, ignore_index=True)


In [273]:
# Example: build shotchart data for Stephen Curry over a selected subset of seasons
# Results are cached to CSV to avoid repeated API calls

curry_id = player_map.get('Stephen Curry')

if curry_id is None:
    print("Stephen Curry not found in player_map. Please run previous cells first.")
else:
    # Choose key seasons to show evolution: 2012-13, 2015-16, 2018-19, 2021-22, 2024-25
    curry_seasons = ['2012-13', '2015-16', '2018-19', '2021-22', '2024-25']
    
    CURRY_CACHE_FILE = 'curry_shotchart_cache.csv'
    
    # Try to load from cache first
    if os.path.exists(CURRY_CACHE_FILE):
        print(f'Loading cached shot chart data from {CURRY_CACHE_FILE}...')
        df_curry_shots = pd.read_csv(CURRY_CACHE_FILE)
        print(f'Loaded {len(df_curry_shots)} shots from cache.')
        print(f'Seasons in cache: {sorted(df_curry_shots["SEASON"].unique())}')
    else:
        print('Cache not found. Fetching from NBA API...')
        print(f'Fetching seasons: {curry_seasons}')
        df_curry_shots = fetch_shotchart_for_player_seasons(curry_id, curry_seasons)
        if not df_curry_shots.empty:
            # Save to cache
            df_curry_shots.to_csv(CURRY_CACHE_FILE, index=False)
            print(f'Saved {len(df_curry_shots)} shots to {CURRY_CACHE_FILE}')
        else:
            print('No data was fetched. Check API connection.')
    
    # Show summary
    if 'df_curry_shots' in locals() and not df_curry_shots.empty:
        print(f'\nData summary:')
        print(f'  Total shots: {len(df_curry_shots)}')
        print(f'  Seasons: {sorted(df_curry_shots["SEASON"].unique())}')
        print(f'  Columns: {df_curry_shots.columns.tolist()[:10]}')
        df_curry_shots.head()
    else:
        df_curry_shots = pd.DataFrame()
        print('No shot data available.')


Loading cached shot chart data from curry_shotchart_cache.csv...
Loaded 6808 shots from cache.
Seasons in cache: ['2012-13', '2015-16', '2018-19', '2021-22', '2024-25']

Data summary:
  Total shots: 6808
  Seasons: ['2012-13', '2015-16', '2018-19', '2021-22', '2024-25']
  Columns: ['GRID_TYPE', 'GAME_ID', 'GAME_EVENT_ID', 'PLAYER_ID', 'PLAYER_NAME', 'TEAM_ID', 'TEAM_NAME', 'PERIOD', 'MINUTES_REMAINING', 'SECONDS_REMAINING']


In [277]:
# Shot locations for Stephen Curry with interactive season selector

print(f'Creating shot location chart with {len(df_curry_shots)} shots')

# === INTERACTIVE CONTROLS ===

seasons = sorted(df_curry_shots['SEASON'].unique())
season_dropdown = alt.binding_select(options=seasons, name='Season ')
season_select = alt.selection_point(
    fields=['SEASON'],
    bind=season_dropdown,
    value=seasons[0]
)

# === SHOT VISUALIZATION ===

shots = alt.Chart(df_curry_shots).mark_circle(
    size=50, 
    opacity=0.7,
    strokeWidth=1,
    stroke='white'
).encode(
    x=alt.X('LOC_X:Q', 
            scale=alt.Scale(domain=[-260, 260]),
            title='Court X Location (ft)',
            axis=alt.Axis(
                labelFontSize=12,
                titleFontSize=14,
                titleFontWeight='bold',
                labelColor='white',
                titleColor='white',
                gridColor='#444444'
            )),
    y=alt.Y('LOC_Y:Q',
            scale=alt.Scale(domain=[-60, 474]),
            title='Court Y Location (ft)',
            axis=alt.Axis(
                labelFontSize=12,
                titleFontSize=14,
                titleFontWeight='bold',
                labelColor='white',
                titleColor='white',
                gridColor='#444444'
            )),
    color=alt.condition(
        'datum.SHOT_MADE_FLAG == 1',
        alt.value('#00D26A'),  # Green for made
        alt.value('#FF4757')   # Red for missed
    ),
    tooltip=[
        alt.Tooltip('SEASON:N', title='Season'),
        alt.Tooltip('SHOT_MADE_FLAG:N', title='Made'),
        alt.Tooltip('SHOT_DISTANCE:Q', title='Distance (ft)', format='.1f'),
        alt.Tooltip('SHOT_TYPE:N', title='Shot Type'),
        alt.Tooltip('ACTION_TYPE:N', title='Action'),
        alt.Tooltip('SHOT_ZONE_BASIC:N', title='Zone')
    ]
).add_params(
    season_select
).transform_filter(
    season_select
)

shot_chart_viz4 = shots.properties(
    title=alt.Title(
        text='Stephen Curry Shot Locations by Season',
        subtitle='Green = Made | Red = Missed | Use dropdown to select season',
        fontSize=18,
        fontWeight='bold',
        anchor='start',
        color='white'
    ),
    width=650,
    height=718,
    background='#1a1a1a'
).configure_view(
    strokeWidth=0
)

shot_chart_viz4


Creating shot location chart with 6808 shots


alt.Chart(...)